In [13]:
from bs4 import BeautifulSoup
import requests
import pandas as pd
import numpy as np
from selenium import webdriver
from selenium.webdriver.common.by import By
from selenium.webdriver.common.keys import Keys
from selenium.common.exceptions import NoSuchElementException
import time

#Set up DF
cols = [ 'Title', 'Authors', 'Publication Year', 'Abstract', 'Journal/Source', 'Citation', 'Publication Date', 'DOI', 'Time Stamp', 'Query Parameters', 'Search Engine']

df = pd.DataFrame(columns=cols)
df

def scrape_google_scholar(parameter):
    data_row = []
    #Using webdriver to go to Google Scholar
    driver = webdriver.Chrome()
    driver.get("https://scholar.google.com/schhp?hl=en&as_sdt=0,48")

    #Finding search bar, inputting parameter and hitting enter
    search = driver.find_element(By.NAME, 'q')
    search.send_keys(parameter)
    time.sleep(5)
    search.send_keys(Keys.RETURN)

    #getting current url for BS webscrapping, setting up lists for DF
    url = driver.current_url

    #Scraping title, link, authors, and description, adding to lists then adding lists to DF
    response=requests.get(url)
    soup = BeautifulSoup(response.content, 'lxml')
  
    for item in soup.select('[data-lid]'):
        t = item.select('h3')[0].get_text()
        data_row.append(t)
        l = item.select('a')[0]['href']
        data_row.append(l)
        a = item.select('.gs_a')[0].get_text()
        data_row.append(a)
        d = item.select('.gs_rs')[0].get_text()
        data_row.append(d)
        time.sleep((30-5)*np.random.random()+5) #from 5 to 30 seconds
        print(data_row)

#Function to check if there is a next button on the page
def check_next_exists(driver, xpath):
    try:
        driver.find_element(By.XPATH,xpath)
    except NoSuchElementException:
        return False
    return True

more_pages = True

#While there is a next button on the webpage, scrap the webpage and add to dataframe, stop where there is no next button
while more_pages == True:
    for item in soup.select('[data-lid]'):
        t = item.select('h3')[0].get_text()
        titles.append(t)
        l = item.select('a')[0]['href']
        links.append(l)
        a = item.select('.gs_a')[0].get_text()
        authors.append(a)
        d = item.select('.gs_rs')[0].get_text()
        description.append(d)
    time.sleep((30-5)*np.random.random()+5) #from 5 to 30 seconds
    next_page = driver.find_element(By.XPATH, '//*[@id="gs_n"]/center/table/tbody/tr/td[12]/a/b')
    next_page.click()
    more_pages = check_next_exists(driver, "//*[@id='gs_n']/center/table/tbody/tr/td[12]/a/b")
    
scrape_google_scholar("bats")


In [10]:
from serpapi import GoogleSearch
from urllib.parse import urlsplit, parse_qsl

def scrape_google_scholar():
    
    
    #Parameters including API key, search engine, query, language, years of publications, start page
    params = {
    "api_key": "1cb4f93885088ed3fdedea0a19f88e68abc90a4e8b67ab487b19662af808c567",         
    "engine": "google_scholar",
    "q": "serology+bat",  # search query
    "hl": "en",        # language
    "as_ylo": "2018",  # from 2017
    "as_yhi": "2023",  # to 2023
    "start": "0"       # first page
    "num": "20"        #max number of results
}

    search = GoogleSearch(params)

    data_row = []

    while_loop_true = True

    #Search until there is no next option, then set while_loop_true to false once there aren't anymore pages
    while while_loop_true:
        results = search.get_dict()

        print(f"Currently extracting page {results['serpapi_pagination']['current']}..")

        for result in results["organic_results"]:
            title = result["title"]
            publication_info_summary = result["publication_info"]["summary"]
            result_id = result["result_id"]
            link = result.get("link")
            description = result.get("snippet")

            try:
              file_title = result["resources"][0]["title"]
            except: file_title = None

            try:
              file_link = result["resources"][0]["link"]
            except: file_link = None

            try:
              file_format = result["resources"][0]["file_format"]
            except: file_format = None

            try:
              cited_by_count = int(result["inline_links"]["cited_by"]["total"])
            except: cited_by_count = None

            cited_by_id = result.get("inline_links", {}).get("cited_by", {}).get("cites_id", {})
            cited_by_link = result.get("inline_links", {}).get("cited_by", {}).get("link", {})

            try:
              total_versions = int(result["inline_links"]["versions"]["total"])
            except: total_versions = None

            all_versions_link = result.get("inline_links", {}).get("versions", {}).get("link", {})
            all_versions_id = result.get("inline_links", {}).get("versions", {}).get("cluster_id", {})

            data_row.append({
              "page_number": results["serpapi_pagination"]["current"],
              "position": position + 1,
              "result_type": result_type,
              "title": title,
              "link": link,
              "result_id": result_id,
              "publication_info_summary": publication_info_summary,
              "snippet": snippet,
              "cited_by_count": cited_by_count,
              "cited_by_link": cited_by_link,
              "cited_by_id": cited_by_id,
              "total_versions": total_versions,
              "all_versions_link": all_versions_link,
              "all_versions_id": all_versions_id,
              "file_format": file_format,
              "file_title": file_title,
              "file_link": file_link,
            })

        print(data_row)
        
        if "next" in results.get("serpapi_pagination", {}):
            search.params_dict.update(dict(parse_qsl(urlsplit(results["serpapi_pagination"]["next"]).query)))
        else:
            loop_is_true = False

    #return data_row

scrape_google_scholar()

https://serpapi.com/search
Currently extracting page 1..
[{'page_number': 1, 'position': 1, 'result_type': None, 'title': 'Disentangling serology to elucidate henipa‐and filovirus transmission in Madagascar fruit bats', 'link': 'https://besjournals.onlinelibrary.wiley.com/doi/abs/10.1111/1365-2656.12985', 'result_id': 'RosggRrS_CsJ', 'publication_info_summary': 'CE Brook, HC Ranaivoson, CC Broder… - Journal of Animal …, 2019 - Wiley Online Library', 'snippet': '… waning antibodies but retained immunity in adult‐age bats. … Our findings suggest that bats may seasonally modulate … transmission hypotheses by which bats are presumed to host …', 'cited_by_count': 36, 'cited_by_link': 'https://scholar.google.com/scholar?cites=3169639249039362886&as_sdt=2005&sciodt=0,5&hl=en', 'cited_by_id': '3169639249039362886', 'total_versions': 17, 'all_versions_link': 'https://scholar.google.com/scholar?cluster=3169639249039362886&hl=en&as_sdt=0,5&as_ylo=2018&as_yhi=2023', 'all_versions_id': '31696392490

Currently extracting page 3..
[{'page_number': 1, 'position': 1, 'result_type': None, 'title': 'Disentangling serology to elucidate henipa‐and filovirus transmission in Madagascar fruit bats', 'link': 'https://besjournals.onlinelibrary.wiley.com/doi/abs/10.1111/1365-2656.12985', 'result_id': 'RosggRrS_CsJ', 'publication_info_summary': 'CE Brook, HC Ranaivoson, CC Broder… - Journal of Animal …, 2019 - Wiley Online Library', 'snippet': '… waning antibodies but retained immunity in adult‐age bats. … Our findings suggest that bats may seasonally modulate … transmission hypotheses by which bats are presumed to host …', 'cited_by_count': 36, 'cited_by_link': 'https://scholar.google.com/scholar?cites=3169639249039362886&as_sdt=2005&sciodt=0,5&hl=en', 'cited_by_id': '3169639249039362886', 'total_versions': 17, 'all_versions_link': 'https://scholar.google.com/scholar?cluster=3169639249039362886&hl=en&as_sdt=0,5&as_ylo=2018&as_yhi=2023', 'all_versions_id': '3169639249039362886', 'file_format': '

Currently extracting page 7..
[{'page_number': 1, 'position': 1, 'result_type': None, 'title': 'Disentangling serology to elucidate henipa‐and filovirus transmission in Madagascar fruit bats', 'link': 'https://besjournals.onlinelibrary.wiley.com/doi/abs/10.1111/1365-2656.12985', 'result_id': 'RosggRrS_CsJ', 'publication_info_summary': 'CE Brook, HC Ranaivoson, CC Broder… - Journal of Animal …, 2019 - Wiley Online Library', 'snippet': '… waning antibodies but retained immunity in adult‐age bats. … Our findings suggest that bats may seasonally modulate … transmission hypotheses by which bats are presumed to host …', 'cited_by_count': 36, 'cited_by_link': 'https://scholar.google.com/scholar?cites=3169639249039362886&as_sdt=2005&sciodt=0,5&hl=en', 'cited_by_id': '3169639249039362886', 'total_versions': 17, 'all_versions_link': 'https://scholar.google.com/scholar?cluster=3169639249039362886&hl=en&as_sdt=0,5&as_ylo=2018&as_yhi=2023', 'all_versions_id': '3169639249039362886', 'file_format': '

Currently extracting page 11..
[{'page_number': 1, 'position': 1, 'result_type': None, 'title': 'Disentangling serology to elucidate henipa‐and filovirus transmission in Madagascar fruit bats', 'link': 'https://besjournals.onlinelibrary.wiley.com/doi/abs/10.1111/1365-2656.12985', 'result_id': 'RosggRrS_CsJ', 'publication_info_summary': 'CE Brook, HC Ranaivoson, CC Broder… - Journal of Animal …, 2019 - Wiley Online Library', 'snippet': '… waning antibodies but retained immunity in adult‐age bats. … Our findings suggest that bats may seasonally modulate … transmission hypotheses by which bats are presumed to host …', 'cited_by_count': 36, 'cited_by_link': 'https://scholar.google.com/scholar?cites=3169639249039362886&as_sdt=2005&sciodt=0,5&hl=en', 'cited_by_id': '3169639249039362886', 'total_versions': 17, 'all_versions_link': 'https://scholar.google.com/scholar?cluster=3169639249039362886&hl=en&as_sdt=0,5&as_ylo=2018&as_yhi=2023', 'all_versions_id': '3169639249039362886', 'file_format': 

https://serpapi.com/search
Currently extracting page 15..
[{'page_number': 1, 'position': 1, 'result_type': None, 'title': 'Disentangling serology to elucidate henipa‐and filovirus transmission in Madagascar fruit bats', 'link': 'https://besjournals.onlinelibrary.wiley.com/doi/abs/10.1111/1365-2656.12985', 'result_id': 'RosggRrS_CsJ', 'publication_info_summary': 'CE Brook, HC Ranaivoson, CC Broder… - Journal of Animal …, 2019 - Wiley Online Library', 'snippet': '… waning antibodies but retained immunity in adult‐age bats. … Our findings suggest that bats may seasonally modulate … transmission hypotheses by which bats are presumed to host …', 'cited_by_count': 36, 'cited_by_link': 'https://scholar.google.com/scholar?cites=3169639249039362886&as_sdt=2005&sciodt=0,5&hl=en', 'cited_by_id': '3169639249039362886', 'total_versions': 17, 'all_versions_link': 'https://scholar.google.com/scholar?cluster=3169639249039362886&hl=en&as_sdt=0,5&as_ylo=2018&as_yhi=2023', 'all_versions_id': '3169639249

...

IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
NotebookApp.rate_limit_window=3.0 (secs)



Currently extracting page 57..
[{'page_number': 1, 'position': 1, 'result_type': None, 'title': 'Disentangling serology to elucidate henipa‐and filovirus transmission in Madagascar fruit bats', 'link': 'https://besjournals.onlinelibrary.wiley.com/doi/abs/10.1111/1365-2656.12985', 'result_id': 'RosggRrS_CsJ', 'publication_info_summary': 'CE Brook, HC Ranaivoson, CC Broder… - Journal of Animal …, 2019 - Wiley Online Library', 'snippet': '… waning antibodies but retained immunity in adult‐age bats. … Our findings suggest that bats may seasonally modulate … transmission hypotheses by which bats are presumed to host …', 'cited_by_count': 36, 'cited_by_link': 'https://scholar.google.com/scholar?cites=3169639249039362886&as_sdt=2005&sciodt=0,5&hl=en', 'cited_by_id': '3169639249039362886', 'total_versions': 17, 'all_versions_link': 'https://scholar.google.com/scholar?cluster=3169639249039362886&hl=en&as_sdt=0,5&as_ylo=2018&as_yhi=2023', 'all_versions_id': '3169639249039362886', 'file_format': 

IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
NotebookApp.rate_limit_window=3.0 (secs)




https://serpapi.com/search
Currently extracting page 96..
[{'page_number': 1, 'position': 1, 'result_type': None, 'title': 'Disentangling serology to elucidate henipa‐and filovirus transmission in Madagascar fruit bats', 'link': 'https://besjournals.onlinelibrary.wiley.com/doi/abs/10.1111/1365-2656.12985', 'result_id': 'RosggRrS_CsJ', 'publication_info_summary': 'CE Brook, HC Ranaivoson, CC Broder… - Journal of Animal …, 2019 - Wiley Online Library', 'snippet': '… waning antibodies but retained immunity in adult‐age bats. … Our findings suggest that bats may seasonally modulate … transmission hypotheses by which bats are presumed to host …', 'cited_by_count': 36, 'cited_by_link': 'https://scholar.google.com/scholar?cites=3169639249039362886&as_sdt=2005&sciodt=0,5&hl=en', 'cited_by_id': '3169639249039362886', 'total_versions': 17, 'all_versions_link': 'https://scholar.google.com/scholar?cluster=3169639249039362886&hl=en&as_sdt=0,5&as_ylo=2018&as_yhi=2023', 'all_versions_id': '316963924

KeyError: 'serpapi_pagination'